In [0]:
#!cat /proc/meminfo
# Uncomment if want to use
'''
System Specs
!df -h
!cat /proc/cpuinfo
!cat /proc/meminfo


Project related links - 
https://github.com/lars76/object-localization
https://lars76.github.io/neural-networks/object-detection/obj-detection-from-scratch/#
https://github.com/DemonFuneral/Image-Object-Localization/tree/master/src
'''

'\nSystem Specs\n!df -h\n!cat /proc/cpuinfo\n!cat /proc/meminfo\n\n\nProject related links - \nhttps://github.com/lars76/object-localization\nhttps://lars76.github.io/neural-networks/object-detection/obj-detection-from-scratch/#\nhttps://github.com/DemonFuneral/Image-Object-Localization/tree/master/src\n'

In [0]:
# Download dataset
!wget http://download2263.mediafire.com/1ym05lb6v59g/3v3na7c5do9s6zw/training.csv
#!wget https://d8it4huxumps7.cloudfront.net/uploads/attachements/code-contests/flipkartgrid/test.csv
#!wget http://www.mediafire.com/file/ue7q4i4ap52okm4/images.zip | tar -xvzf


--2019-02-02 05:33:24--  http://download2263.mediafire.com/1ym05lb6v59g/3v3na7c5do9s6zw/training.csv
Resolving download2263.mediafire.com (download2263.mediafire.com)... 199.91.155.4
Connecting to download2263.mediafire.com (download2263.mediafire.com)|199.91.155.4|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 717902 (701K) [text/plain]
Saving to: ‘training.csv’

training.csv        100%[===================>] 701.08K  4.31MB/s    in 0.2s    

2019-02-02 05:33:24 (4.31 MB/s) - ‘training.csv’ saved [717902/717902]



In [0]:
!wget http://download2325.mediafire.com/7hteztyv4ozg/ue7q4i4ap52okm4/images.zip
!unzip images.zip -d image

--2019-02-02 03:54:20--  http://download2325.mediafire.com/7hteztyv4ozg/ue7q4i4ap52okm4/images.zip
Resolving download2325.mediafire.com (download2325.mediafire.com)... 199.91.155.66
Connecting to download2325.mediafire.com (download2325.mediafire.com)|199.91.155.66|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 14162995388 (13G) [application/zip]
Saving to: ‘images.zip’

images.zip          100%[===================>]  13.19G  7.18MB/s    in 32m 41s 

2019-02-02 04:27:01 (6.89 MB/s) - ‘images.zip’ saved [14162995388/14162995388]

Archive:  images.zip
   creating: image/images/
  inflating: image/images/1474638867554DSC06870.png  
  inflating: image/images/1474289982252light-blue-daily-double-tiered-dress2.png  
  inflating: image/images/JPEG_20161123_185318_100014949781.png  
  inflating: image/images/1473664947766DeeplearnS11724.png  
  inflating: image/images/1475816819497black-nude-darkest-desire-lace-bodycon-dress4.png  
  inflating: image/images/JPEG_20160

In [0]:
from PIL import Image
import pandas as pd
from sklearn import preprocessing as pre
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import pickle
import random

import keras
import tensorflow as tf
from keras.layers import Dense, Conv2D, BatchNormalization, Activation
from keras.layers import AveragePooling2D, MaxPooling2D, Input, Flatten
from keras.optimizers import Adam
from keras.regularizers import l2
from keras import backend as K
from keras.models import Model,load_model
from keras.callbacks import ModelCheckpoint,LearningRateScheduler,ReduceLROnPlateau
import numpy as np

plt.switch_backend('agg')

def getdata():
    id_to_data={}
    id_to_size={}
    f1 = pd.read_csv('./training.csv')

    for index, row in f1.iterrows():
        if index == 7000:
            break
        image=Image.open("./image/images/"+row['image_name']).convert('RGB')
        id_to_size[index]=np.array(image,dtype=np.float32).shape[0:2]
        image=image.resize((224,224))
        image=np.array(image,dtype=np.float32)
        print('Image loading : ' + str(index) + '\n')
        image=image/255
        pre.normalize(image[0])#Normalize(image,[0.485,0.456,0.406],[0.229,0.224,0.225])
        pre.normalize(image[1])
        pre.normalize(image[2])
        id_to_data[index]=image

    id_to_data=np.array(list(id_to_data.values()))
    id_to_size=np.array(list(id_to_size.values()))

    id_to_box={}

    for index, row in f1.iterrows():
        if index == 7000:
            break
        box = np.array([float(i) for i in range(4)], dtype = np.float32)
        box[0]=row['x1']/id_to_size[index][1]*224
        box[1]=row['y1']/id_to_size[index][0]*224
        box[2]=row['x2']/id_to_size[index][1]*224
        box[3]=row['y2']/id_to_size[index][0]*224
        id_to_box[index]=box

    id_to_box=np.array(list(id_to_box.values()))
    return id_to_data, id_to_box


def plot_model(model_details):
    fig, axs = plt.subplots(1,2,figsize=(15,5))

    axs[0].plot(range(1,len(model_details.history['my_metric'])+1),model_details.history['my_metric'])
    axs[0].plot(range(1,len(model_details.history['val_my_metric'])+1),[1.7*x for x in model_details.history['val_my_metric']])
    axs[0].set_title('Model Accuracy')
    axs[0].set_ylabel('Accuracy')
    axs[0].set_xlabel('Epoch')
    axs[0].set_xticks(np.arange(1,len(model_details.history['my_metric'])+1),len(model_details.history['my_metric'])/10)
    axs[0].legend(['train', 'val'], loc='best')

    axs[1].plot(range(1,len(model_details.history['loss'])+1),model_details.history['loss'])
    axs[1].plot(range(1,len(model_details.history['val_loss'])+1),model_details.history['val_loss'])
    axs[1].set_title('Model Loss')
    axs[1].set_ylabel('Loss')
    axs[1].set_xlabel('Epoch')
    axs[1].set_xticks(np.arange(1,len(model_details.history['loss'])+1),len(model_details.history['loss'])/10)
    axs[1].legend(['train', 'val'], loc='best')

    plt.savefig("model.png")



data_train,box_train=getdata()

# metric function
def my_metric(labels,predictions):
    threshhold=0.75
    x=predictions[:,0]*224
    x=tf.maximum(tf.minimum(x,224.0),0.0)
    y=predictions[:,1]*224
    y=tf.maximum(tf.minimum(y,224.0),0.0)
    width=predictions[:,2]*224
    width=tf.maximum(tf.minimum(width,224.0),0.0)
    height=predictions[:,3]*224
    height=tf.maximum(tf.minimum(height,224.0),0.0)
    label_x=labels[:,0]
    label_y=labels[:,1]
    label_width=labels[:,2]
    label_height=labels[:,3]
    a1=tf.multiply(width,height)
    a2=tf.multiply(label_width,label_height)
    x1=tf.maximum(x,label_x)
    y1=tf.maximum(y,label_y)
    x2=tf.minimum(x+width,label_x+label_width)
    y2=tf.minimum(y+height,label_y+label_height)
    IoU=tf.abs(tf.multiply((x1-x2),(y1-y2)))/(a1+a2-tf.abs(tf.multiply((x1-x2),(y1-y2))))
    condition=tf.less(threshhold,IoU)
    sum=tf.where(condition,tf.ones(tf.shape(condition)),tf.zeros(tf.shape(condition)))
    return tf.reduce_mean(sum)

# loss function
def smooth_l1_loss(true_box,pred_box):
    loss=0.0
    for i in range(4):
        residual=tf.abs(true_box[:,i]-pred_box[:,i]*224)
        condition=tf.less(residual,1.0)
        small_res=0.5*tf.square(residual)
        large_res=residual-0.5
        loss=loss+tf.where(condition,small_res,large_res)
    return tf.reduce_mean(loss)


def resnet_block(inputs,num_filters,kernel_size,strides,activation='relu'):
    x=Conv2D(num_filters,kernel_size=kernel_size,strides=strides,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(inputs)
    x=BatchNormalization()(x)
    if(activation):
        x=Activation('relu')(x)
    return x


def resnet18():
    inputs=Input((224,224,3))
    
    # conv1
    x=resnet_block(inputs,64,[7,7],2)

    # conv2
    x=MaxPooling2D([3,3],2,'same')(x)
    for i in range(2):
        a=resnet_block(x,64,[3,3],1)
        b=resnet_block(a,64,[3,3],1)
        c=resnet_block(b,64,[3,3],1,activation=None)
        x=keras.layers.add([x,c])
        x=Activation('relu')(x)
    
    # conv3
    a=resnet_block(x,128,[1,1],2)
    b=resnet_block(a,128,[3,3],1)
    c=resnet_block(b,128,[3,3],1)
    d=resnet_block(c,128,[3,3],1,activation=None)
    x=Conv2D(128,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,d])
    x=Activation('relu')(x)

    a=resnet_block(x,128,[3,3],1)
    b=resnet_block(a,128,[3,3],1)
    c=resnet_block(b,128,[3,3],1)
    d=resnet_block(c,128,[3,3],1,activation=None)
    x=keras.layers.add([x,d])
    x=Activation('relu')(x)

    # conv4
    a=resnet_block(x,256,[1,1],2)
    b=resnet_block(a,256,[3,3],1)
    c=resnet_block(b,256,[3,3],1)
    d=resnet_block(c,256,[3,3],1)
    e=resnet_block(d,256,[3,3],1)
    f=resnet_block(e,256,[3,3],1,activation=None)
    x=Conv2D(256,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,f])
    x=Activation('relu')(x)

    a=resnet_block(x,256,[3,3],1)
    b=resnet_block(a,256,[3,3],1)
    c=resnet_block(b,256,[3,3],1)
    d=resnet_block(c,256,[3,3],1)
    e=resnet_block(d,256,[3,3],1)
    f=resnet_block(e,256,[3,3],1,activation=None)
    x=keras.layers.add([x,f])
    x=Activation('relu')(x)

    # conv5
    a=resnet_block(x,512,[1,1],2)
    b=resnet_block(a,512,[3,3],1)
    c=resnet_block(b,512,[3,3],1,activation=None)
    x=Conv2D(512,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,c])
    x=Activation('relu')(x)

    a=resnet_block(x,512,[3,3],1)
    b=resnet_block(a,512,[3,3],1)
    c=resnet_block(b,512,[3,3],1,activation=None)
    x=keras.layers.add([x,c])
    x=Activation('relu')(x)

    x=AveragePooling2D(pool_size=7,data_format="channels_last")(x)
    # out:1*1*512

    y=Flatten()(x)
    # out:512
    y=Dense(1000,kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(y)
    outputs=Dense(4,kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(y)
    
    model=Model(inputs=inputs,outputs=outputs)
    return model

model = resnet18()


#model.compile(loss="smooth_l1_loss",optimizer=Adam(),metrics=["my_metric"])
model.compile(loss=smooth_l1_loss,optimizer=Adam(), metrics=[my_metric])

model.summary()

def lr_sch(epoch):
    #200 total
    if epoch <50:
        return 1e-3
    if 50<=epoch<100:
        return 1e-4
    if epoch>=100:
        return 1e-5

lr_scheduler=LearningRateScheduler(lr_sch)
lr_reducer=ReduceLROnPlateau(monitor='val_my_metric',factor=0.2,patience=5,mode='max',min_lr=1e-3)

checkpoint=ModelCheckpoint('50model.h5',monitor='val_loss',verbose=0,save_best_only=True,mode='auto')

model_details=model.fit(data_train,box_train,batch_size=128,epochs=50,shuffle=True,validation_split=0.1,callbacks=[lr_scheduler,lr_reducer,checkpoint],verbose=1)

model.save('50model.h5')

plot_model(model_details)


Using TensorFlow backend.


Image loading : 0

Image loading : 1

Image loading : 2

Image loading : 3

Image loading : 4

Image loading : 5

Image loading : 6

Image loading : 7

Image loading : 8

Image loading : 9

Image loading : 10

Image loading : 11

Image loading : 12

Image loading : 13

Image loading : 14

Image loading : 15

Image loading : 16

Image loading : 17

Image loading : 18

Image loading : 19

Image loading : 20

Image loading : 21

Image loading : 22

Image loading : 23

Image loading : 24

Image loading : 25

Image loading : 26

Image loading : 27

Image loading : 28

Image loading : 29

Image loading : 30

Image loading : 31

Image loading : 32

Image loading : 33

Image loading : 34

Image loading : 35

Image loading : 36

Image loading : 37

Image loading : 38

Image loading : 39

Image loading : 40

Image loading : 41

Image loading : 42

Image loading : 43

Image loading : 44

Image loading : 45

Image loading : 46

Image loading : 47

Image loading : 48

Image loading : 49

Image load

In [0]:
from PIL import Image
import pandas as pd
from sklearn import preprocessing as pre
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import pickle
import random

import keras
import tensorflow as tf
from keras.layers import Dense, Conv2D, BatchNormalization, Activation
from keras.layers import AveragePooling2D, MaxPooling2D, Input, Flatten
from keras.optimizers import Adam
from keras.regularizers import l2
from keras import backend as K
from keras.models import Model,load_model
from keras.callbacks import ModelCheckpoint,LearningRateScheduler,ReduceLROnPlateau
import numpy as np

plt.switch_backend('agg')

def getdata():
    id_to_data={}
    id_to_size={}
    f1 = pd.read_csv('./training.csv')

    for index, row in f1.iterrows():
        if index < 7000:
            #index = index - 7001
            image=Image.open("./image/images/"+row['image_name']).convert('RGB')
            id_to_size[index]=np.array(image,dtype=np.float32).shape[0:2]
            image=image.resize((224,224))
            image=np.array(image,dtype=np.float32)
            print('Image loading : ' + str(index) + '\n')
            image=image/255
            pre.normalize(image[0])#Normalize(image,[0.485,0.456,0.406],[0.229,0.224,0.225])
            pre.normalize(image[1])
            pre.normalize(image[2])
            id_to_data[index]=image

    id_to_data=np.array(list(id_to_data.values()))
    id_to_size=np.array(list(id_to_size.values()))

    id_to_box={}

    for index, row in f1.iterrows():
        if index < 7000:
            #index = index - 7001
            box = np.array([float(i) for i in range(4)], dtype = np.float32)
            box[0]=row['x1']/id_to_size[index][1]*224
            box[1]=row['y1']/id_to_size[index][0]*224
            box[2]=row['x2']/id_to_size[index][1]*224
            box[3]=row['y2']/id_to_size[index][0]*224
            id_to_box[index]=box

    id_to_box=np.array(list(id_to_box.values()))
    return id_to_data, id_to_box


def plot_model(model_details):
    fig, axs = plt.subplots(1,2,figsize=(15,5))

    axs[0].plot(range(1,len(model_details.history['my_metric'])+1),model_details.history['my_metric'])
    axs[0].plot(range(1,len(model_details.history['val_my_metric'])+1),[1.7*x for x in model_details.history['val_my_metric']])
    axs[0].set_title('Model Accuracy')
    axs[0].set_ylabel('Accuracy')
    axs[0].set_xlabel('Epoch')
    axs[0].set_xticks(np.arange(1,len(model_details.history['my_metric'])+1),len(model_details.history['my_metric'])/10)
    axs[0].legend(['train', 'val'], loc='best')

    axs[1].plot(range(1,len(model_details.history['loss'])+1),model_details.history['loss'])
    axs[1].plot(range(1,len(model_details.history['val_loss'])+1),model_details.history['val_loss'])
    axs[1].set_title('Model Loss')
    axs[1].set_ylabel('Loss')
    axs[1].set_xlabel('Epoch')
    axs[1].set_xticks(np.arange(1,len(model_details.history['loss'])+1),len(model_details.history['loss'])/10)
    axs[1].legend(['train', 'val'], loc='best')

    plt.savefig("model.png")



data_train,box_train=getdata()

# metric function
def my_metric(labels,predictions):
    threshhold=0.75
    x=predictions[:,0]*224
    x=tf.maximum(tf.minimum(x,224.0),0.0)
    y=predictions[:,1]*224
    y=tf.maximum(tf.minimum(y,224.0),0.0)
    width=predictions[:,2]*224
    width=tf.maximum(tf.minimum(width,224.0),0.0)
    height=predictions[:,3]*224
    height=tf.maximum(tf.minimum(height,224.0),0.0)
    label_x=labels[:,0]
    label_y=labels[:,1]
    label_width=labels[:,2]
    label_height=labels[:,3]
    a1=tf.multiply(width,height)
    a2=tf.multiply(label_width,label_height)
    x1=tf.maximum(x,label_x)
    y1=tf.maximum(y,label_y)
    x2=tf.minimum(x+width,label_x+label_width)
    y2=tf.minimum(y+height,label_y+label_height)
    IoU=tf.abs(tf.multiply((x1-x2),(y1-y2)))/(a1+a2-tf.abs(tf.multiply((x1-x2),(y1-y2))))
    condition=tf.less(threshhold,IoU)
    sum=tf.where(condition,tf.ones(tf.shape(condition)),tf.zeros(tf.shape(condition)))
    return tf.reduce_mean(sum)

# loss function
def smooth_l1_loss(true_box,pred_box):
    loss=0.0
    for i in range(4):
        residual=tf.abs(true_box[:,i]-pred_box[:,i]*224)
        condition=tf.less(residual,1.0)
        small_res=0.5*tf.square(residual)
        large_res=residual-0.5
        loss=loss+tf.where(condition,small_res,large_res)
    return tf.reduce_mean(loss)


def resnet_block(inputs,num_filters,kernel_size,strides,activation='relu'):
    x=Conv2D(num_filters,kernel_size=kernel_size,strides=strides,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(inputs)
    x=BatchNormalization()(x)
    if(activation):
        x=Activation('relu')(x)
    return x


def resnet18():
    inputs=Input((224,224,3))
    
    # conv1
    x=resnet_block(inputs,64,[7,7],2)

    # conv2
    x=MaxPooling2D([3,3],2,'same')(x)
    for i in range(2):
        a=resnet_block(x,64,[3,3],1)
        b=resnet_block(a,64,[3,3],1,activation=None)
        x=keras.layers.add([x,b])
        x=Activation('relu')(x)
    
    # conv3
    a=resnet_block(x,128,[1,1],2)
    b=resnet_block(a,128,[3,3],1,activation=None)
    x=Conv2D(128,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    a=resnet_block(x,128,[3,3],1)
    b=resnet_block(a,128,[3,3],1,activation=None)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    # conv4
    a=resnet_block(x,256,[1,1],2)
    b=resnet_block(a,256,[3,3],1,activation=None)
    x=Conv2D(256,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    a=resnet_block(x,256,[3,3],1)
    b=resnet_block(a,256,[3,3],1,activation=None)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    # conv5
    a=resnet_block(x,512,[1,1],2)
    b=resnet_block(a,512,[3,3],1,activation=None)
    x=Conv2D(512,kernel_size=[1,1],strides=2,padding='same',kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(x)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    a=resnet_block(x,512,[3,3],1)
    b=resnet_block(a,512,[3,3],1,activation=None)
    x=keras.layers.add([x,b])
    x=Activation('relu')(x)

    x=AveragePooling2D(pool_size=7,data_format="channels_last")(x)
    # out:1*1*512

    y=Flatten()(x)
    # out:512
    y=Dense(1000,kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(y)
    outputs=Dense(4,kernel_initializer='he_normal',kernel_regularizer=l2(1e-3))(y)
    
    model=Model(inputs=inputs,outputs=outputs)
    return model

print("Loading model \n")
model = load_model('new_model.h5', custom_objects={'smooth_l1_loss': smooth_l1_loss, 'my_metric': my_metric})
model.summary()
print("Loaded model \n")

def lr_sch(epoch):
    #200 total
    if epoch <50:
        return 1e-3
    if 50<=epoch<100:
        return 1e-4
    if epoch>=100:
        return 1e-5

lr_scheduler=LearningRateScheduler(lr_sch)
lr_reducer=ReduceLROnPlateau(monitor='val_my_metric',factor=0.2,patience=5,mode='max',min_lr=1e-3)

checkpoint=ModelCheckpoint('model.h5',monitor='val_loss',verbose=0,save_best_only=True,mode='auto')

model_details=model.fit(data_train,box_train,batch_size=128,epochs=40,shuffle=True,validation_split=0.1,callbacks=[lr_scheduler,lr_reducer,checkpoint],verbose=1)

model.save('model.h5')

plot_model(model_details)


Using TensorFlow backend.


Image loading : 0

Image loading : 1

Image loading : 2

Image loading : 3

Image loading : 4

Image loading : 5

Image loading : 6

Image loading : 7

Image loading : 8

Image loading : 9

Image loading : 10

Image loading : 11

Image loading : 12

Image loading : 13

Image loading : 14

Image loading : 15

Image loading : 16

Image loading : 17

Image loading : 18

Image loading : 19

Image loading : 20

Image loading : 21

Image loading : 22

Image loading : 23

Image loading : 24

Image loading : 25

Image loading : 26

Image loading : 27

Image loading : 28

Image loading : 29

Image loading : 30

Image loading : 31

Image loading : 32

Image loading : 33

Image loading : 34

Image loading : 35

Image loading : 36

Image loading : 37

Image loading : 38

Image loading : 39

Image loading : 40

Image loading : 41

Image loading : 42

Image loading : 43

Image loading : 44

Image loading : 45

Image loading : 46

Image loading : 47

Image loading : 48

Image loading : 49

Image load

In [0]:
#Testing

import pickle
import numpy as np
import matplotlib.pyplot as plt
import keras
from keras.models import load_model
from sklearn import preprocessing as pre
import random
import math

from PIL import Image
import pandas as pd
import keras
import tensorflow as tf
from keras.layers import Dense, Conv2D, BatchNormalization, Activation
from keras.layers import AveragePooling2D, MaxPooling2D, Input, Flatten
from keras.optimizers import Adam
from keras.regularizers import l2
from keras import backend as K
from keras.models import Model,load_model
from keras.callbacks import ModelCheckpoint,LearningRateScheduler,ReduceLROnPlateau
import numpy as np

def my_metric(labels,predictions):
    threshhold=0.75
    x=predictions[:,0]*224
    x=tf.maximum(tf.minimum(x,224.0),0.0)
    y=predictions[:,1]*224
    y=tf.maximum(tf.minimum(y,224.0),0.0)
    width=predictions[:,2]*224
    width=tf.maximum(tf.minimum(width,224.0),0.0)
    height=predictions[:,3]*224
    height=tf.maximum(tf.minimum(height,224.0),0.0)
    label_x=labels[:,0]
    label_y=labels[:,1]
    label_width=labels[:,2]
    label_height=labels[:,3]
    a1=tf.multiply(width,height)
    a2=tf.multiply(label_width,label_height)
    x1=tf.maximum(x,label_x)
    y1=tf.maximum(y,label_y)
    x2=tf.minimum(x+width,label_x+label_width)
    y2=tf.minimum(y+height,label_y+label_height)
    IoU=tf.abs(tf.multiply((x1-x2),(y1-y2)))/(a1+a2-tf.abs(tf.multiply((x1-x2),(y1-y2))))
    condition=tf.less(threshhold,IoU)
    sum=tf.where(condition,tf.ones(tf.shape(condition)),tf.zeros(tf.shape(condition)))
    return tf.reduce_mean(sum)

# loss function
def smooth_l1_loss(true_box,pred_box):
    loss=0.0
    for i in range(4):
        residual=tf.abs(true_box[:,i]-pred_box[:,i]*224)
        condition=tf.less(residual,1.0)
        small_res=0.5*tf.square(residual)
        large_res=residual-0.5
        loss=loss+tf.where(condition,small_res,large_res)
    return tf.reduce_mean(loss)

plt.switch_backend('agg')

id_to_data={}
id_to_size={}
f1 = pd.read_csv('./test.csv')

for index, row in f1.iterrows():
    if index >= 7000:
        index = index - 7000
        image=Image.open("./image/images/"+row['image_name']).convert('RGB')
        id_to_size[index]=np.array(image,dtype=np.float32).shape[0:2]
        image=image.resize((224,224))
        image=np.array(image,dtype=np.float32)
        print('Image loading : ' + str(index) + '\n')
        image=image/255
        pre.normalize(image[0])#Normalize(image,[0.485,0.456,0.406],[0.229,0.224,0.225])
        pre.normalize(image[1])
        pre.normalize(image[2])
        id_to_data[index]=image

id_to_data=np.array(list(id_to_data.values()))
id_to_size=np.array(list(id_to_size.values()))

model = load_model('model.h5', custom_objects={'smooth_l1_loss': smooth_l1_loss, 'my_metric': my_metric})

result=model.predict(id_to_data)

csv={}
for i in range(12815 - 7000):
    print("Predicting "+str(i)+"th image.")
    image=id_to_data[i]
    prediction=result[i]
    pre.normalize(image[0])
    pre.normalize(image[1])
    pre.normalize(image[2])

    image=image*255
    image=image.astype(np.uint8)
    plt.imshow(image)
    
    box = np.array([float(i) for i in range(5)], dtype = np.int32)
    box[0]=int(round(prediction[0]*(640)))
    box[1]=int(round(prediction[2]*(640)))
    box[2]=int(round(prediction[1]*(480)))
    box[3]=int(round(prediction[3]*(480)))
    csv[i]=box

    #plt.gca().add_patch(plt.Rectangle((prediction[0]*224,prediction[1]*224),(prediction[2] - prediction[0])*224,(prediction[3] - prediction[1])*224,fill=False,edgecolor='green',linewidth=2,alpha=0.5))
    #plt.show()
    #plt.savefig(str(i)+".png")
    #plt.cla()
csv=np.array(list(csv.values()))
np.savetxt("test1.csv", csv, delimiter=",")





Image loading : 0

Image loading : 1

Image loading : 2

Image loading : 3

Image loading : 4

Image loading : 5

Image loading : 6

Image loading : 7

Image loading : 8

Image loading : 9

Image loading : 10

Image loading : 11

Image loading : 12

Image loading : 13

Image loading : 14

Image loading : 15

Image loading : 16

Image loading : 17

Image loading : 18

Image loading : 19

Image loading : 20

Image loading : 21

Image loading : 22

Image loading : 23

Image loading : 24

Image loading : 25

Image loading : 26

Image loading : 27

Image loading : 28

Image loading : 29

Image loading : 30

Image loading : 31

Image loading : 32

Image loading : 33

Image loading : 34

Image loading : 35

Image loading : 36

Image loading : 37

Image loading : 38

Image loading : 39

Image loading : 40

Image loading : 41

Image loading : 42

Image loading : 43

Image loading : 44

Image loading : 45

Image loading : 46

Image loading : 47

Image loading : 48

Image loading : 49

Image load

In [0]:
#New
